In [1]:
import os
import glob
import time
from datetime import timedelta, datetime
import numpy as np
import pandas as pd
import qgrid

from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots

#setting offilne
plotly.offline.init_notebook_mode(connected=True)
import gezi

from projects.feed.rank.monitor.taurus import Taurus

In [2]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [3]:
last_days = 40
start_time = None
end_time = None
# start_time = 20191210
# end_time = 20191220
# abids = [8,15,16]
# abids = [16, 8]
# abids = [16]
# abids = [8, 15]
abids = [15]
# abids = [16]

assert len(abids) == 1, 'FIXME only 1 abid is ok now, as natural_diff wrong currenlty TODO'
product = 'sgsapp'
# product = 'newmse'

diff_spans_ = {
    8: [20200313, 20200319],
#     12: [20190130, 20200205],
#     11: [20190130, 20200205],
    15: [20200325, 20200331],
    16: [20200325, 20200331],
}
diff_spans = {}
for abid in abids:
  diff_spans[abid] = diff_spans_[abid]

# diff_spans = None

In [4]:
worker_daily = Taurus()
worker_daily.init(abids, last_days, 'daily', product=product,
                  diff_spans=diff_spans, start_time=start_time, end_time=end_time)
worker_daily.run()

# for name 1(tuwen,video,small_video,total) 2(quality,total) 3(recommend,relative,total)
def show_daily(name, use_diff=True, quality=False, field=None):
  worker_daily.show(name, quality, field, use_diff=True)

SELECT * FROM feed_abtest_video_type_common_daily 
                WHERE product = 'sgsapp'
                AND abtest in ('6','5','4','15') 
                AND date BETWEEN '20191104' AND '20200415'
                AND video_type not in ('-1', 'NULL')
          
67.11306238174438


In [5]:
w = worker_daily
d = worker_daily.ratio2
d = d.sort_values('date', ascending=False)
# pd.set_option('precision', 5)  
names = ['dis_user', 'click_user', 'click', 'duration', 'refresh_times', 'read_files', 'ctr', 'read_ratio', 'dur1', 'dur2', 
         'doc_dur', 'finish_ratio', 'praise', 'favor', 'share']
# d2 = d[d.name!='small_video'].groupby(['name', 'data_obj', 'abtest']).head(6).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]
d2 = d.groupby(['name', 'data_obj', 'abtest']).head(7).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]

# qgrid.show_grid(d2)
# d2

In [6]:
d_ = d2[d2.data_obj=='total_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [7]:
d_ = d2[d2.data_obj=='quality_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [8]:
d_ = d2[d2.data_obj=='total_relative']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [9]:
w.ratio2[w.ratio2.name=='total'][w.ratio2.data_obj=='total_total']

product_name      date   name     data_obj  abtest        id       dis  \
11         sgsapp  20191104  total  total_total      15 -0.000008  0.007698   
35         sgsapp  20191105  total  total_total      15 -0.000008  0.002529   
59         sgsapp  20191106  total  total_total      15 -0.000008  0.001371   
83         sgsapp  20191107  total  total_total      15 -0.000008  0.009448   
107        sgsapp  20191108  total  total_total      15 -0.000008 -0.006386   
...           ...       ...    ...          ...     ...       ...       ...   
3803       sgsapp  20200410  total  total_total      15 -0.000004  0.037594   
3827       sgsapp  20200411  total  total_total      15 -0.000004  0.024799   
3851       sgsapp  20200412  total  total_total      15 -0.000004  0.028995   
3875       sgsapp  20200413  total  total_total      15 -0.000004  0.032605   
3899       sgsapp  20200414  total  total_total      15 -0.000004  0.040118   

      dis_user  refresh_times  real_dis  ...       ctr  real_ctr  read_ratio  \
11    0.008506       0.007583  0.008772  ... -0.014073 -0.016537    0.008361   
35    0.006402       0.003439  0.002428  ... -0.005253 -0.006549   -0.000154   
59    0.009916       0.007046  0.006523  ... -0.026962 -0.033360   -0.004552   
83    0.009440       0.010461  0.013730  ... -0.019620 -0.025210   -0.011967   
107   0.009468       0.002918  0.006235  ... -0.019455 -0.033205   -0.011305   
...        ...            ...       ...  ...       ...       ...         ...   
3803  0.003938       0.018784  0.029736  ...  0.015499  0.021862    0.017127   
3827 -0.003859       0.007832  0.014498  ...  0.018690  0.027650    0.016621   
3851 -0.004142       0.010597  0.016875  ...  0.028270  0.039137    0.015545   
3875  0.001581       0.014489  0.018826  ...  0.010860  0.023163    0.012602   
3899 -0.002580       0.014152  0.019687  ...  0.043343  0.062922    0.022883   

          dur1      dur2  finish_ratio  read_files   doc_dur   refresh  \
11    0.007603 -0.000620     -0.016788   -0.020448  0.028326 -0.000919   
35    0.045935  0.046285     -0.019788   -0.014693  0.061096 -0.002920   
59    0.015935  0.020763     -0.010701   -0.040700  0.058509 -0.002811   
83   -0.000230  0.012071     -0.007887   -0.025171  0.025281  0.000983   
107  -0.001860  0.009737     -0.035160   -0.040372  0.039632 -0.006440   
...        ...       ...           ...         ...       ...       ...   
3803  0.060319  0.042630      0.002833    0.043774  0.015828  0.014726   
3827  0.061752  0.044554     -0.004467    0.042153  0.018683  0.011677   
3851  0.065274  0.049099     -0.009942    0.056567  0.008156  0.014718   
3875  0.076897  0.063697      0.001007    0.036424  0.038886  0.012835   
3899  0.092606  0.068339     -0.002941    0.082097  0.009709  0.016697   

      refresh2  
11   -0.009216  
35   -0.002773  
59    0.001742  
83    0.013100  
107   0.004905  
...        ...  
3803 -0.002331  
3827 -0.004840  
3851 -0.000800  
3875  0.000247  
3899 -0.006012  

[163 rows x 33 columns]

In [10]:
w.df[w.df.name=='total'][w.df.data_obj=='total_total']

product_name      date   name     data_obj  abtest        id         dis  \
11         sgsapp  20191104  total  total_total      15  10422946  23171568.0   
35         sgsapp  20191105  total  total_total      15  10363544  22254108.0   
59         sgsapp  20191106  total  total_total      15  10304216  24799154.0   
83         sgsapp  20191107  total  total_total      15  10245052  26541782.0   
107        sgsapp  20191108  total  total_total      15  10185984  26077948.0   
...           ...       ...    ...          ...     ...       ...         ...   
3803       sgsapp  20200410  total  total_total      15  19852163  32812704.0   
3827       sgsapp  20200411  total  total_total      15  19977567  32361364.0   
3851       sgsapp  20200412  total  total_total      15  20102237  31259104.0   
3875       sgsapp  20200413  total  total_total      15  20226157  31241974.0   
3899       sgsapp  20200414  total  total_total      15  20661977  31114250.0   

      dis_user  refresh_times   real_dis  ...       ctr  real_ctr  read_ratio  \
11    259940.0      1163350.0  6480136.0  ...  0.060057  0.214753    0.384404   
35    257446.0      1124460.0  6091178.0  ...  0.059478  0.217304    0.383467   
59    262282.0      1169994.0  6605146.0  ...  0.053697  0.201608    0.380956   
83    262096.0      1162376.0  6395246.0  ...  0.050745  0.210604    0.375114   
107   265622.0      1154650.0  6620104.0  ...  0.051393  0.202447    0.371822   
...        ...            ...        ...  ...       ...       ...         ...   
3803  295592.0      1351192.0  7147448.0  ...  0.056446  0.259136    0.353575   
3827  293486.0      1320440.0  7338860.0  ...  0.058406  0.257545    0.344473   
3851  288018.0      1272368.0  7085796.0  ...  0.059208  0.261195    0.347416   
3875  284822.0      1287276.0  7060034.0  ...  0.055012  0.243438    0.341217   
3899  305488.0      1305400.0  6988386.0  ...  0.055448  0.246872    0.326893   

          dur1       dur2  finish_ratio  read_files   doc_dur   refresh  \
11    5.113469  13.302327      0.341759    5.353643  0.955138  4.475456   
35    5.165264  13.469912      0.336266    5.141412  1.004639  4.367751   
59    5.132604  13.472944      0.338454    5.077161  1.010920  4.460825   
83    4.950767  13.198017      0.339902    5.138812  0.963407  4.434925   
107   4.907323  13.198056      0.336563    5.045599  0.972595  4.346967   
...        ...        ...           ...         ...       ...       ...   
3803  6.932244  19.606137      0.286350    6.265927  1.106340  4.571139   
3827  7.071698  20.529035      0.287450    6.440123  1.098069  4.499158   
3851  6.984949  20.105445      0.290829    6.425897  1.087000  4.417668   
3875  6.592867  19.321646      0.301802    6.034225  1.092579  4.519581   
3899  5.971651  18.267887      0.291311    5.647476  1.057402  4.273163   

       refresh2  
11    11.642581  
35    11.390166  
59    11.709542  
83    11.822857  
107   11.691001  
...         ...  
3803  12.928335  
3827  13.060990  
3851  12.715796  
3875  13.245488  
3899  13.072039  

[163 rows x 33 columns]

In [11]:
w.base[w.base.name=='total'][w.base.data_obj=='total_total']

product_name      date   name     data_obj  abtest          id  \
11         sgsapp  20191104  total  total_total     5.0  10423026.0   
35         sgsapp  20191105  total  total_total     5.0  10363624.0   
59         sgsapp  20191106  total  total_total     5.0  10304296.0   
83         sgsapp  20191107  total  total_total     5.0  10245132.0   
107        sgsapp  20191108  total  total_total     5.0  10186064.0   
...           ...       ...    ...          ...     ...         ...   
3803       sgsapp  20200410  total  total_total     5.0  19852243.0   
3827       sgsapp  20200411  total  total_total     5.0  19977647.0   
3851       sgsapp  20200412  total  total_total     5.0  20102317.0   
3875       sgsapp  20200413  total  total_total     5.0  20226237.0   
3899       sgsapp  20200414  total  total_total     5.0  20662057.0   

               dis       dis_user  refresh_times      real_dis  ...       ctr  \
11    2.299455e+07  256682.666667   1.152882e+06  6.423785e+06  ...  0.060755   
35    2.219798e+07  254749.333333   1.118937e+06  6.076425e+06  ...  0.059637   
59    2.476521e+07  258635.333333   1.160083e+06  6.562343e+06  ...  0.055039   
83    2.629337e+07  258573.333333   1.148641e+06  6.308627e+06  ...  0.051624   
107   2.624556e+07  262044.666667   1.149574e+06  6.579084e+06  ...  0.052275   
...            ...            ...            ...           ...  ...       ...   
3803  3.162383e+07  293210.666667   1.324333e+06  6.941050e+06  ...  0.055444   
3827  3.157825e+07  293390.666667   1.308235e+06  7.233982e+06  ...  0.057189   
3851  3.037830e+07  288006.000000   1.257164e+06  6.968207e+06  ...  0.057435   
3875  3.025548e+07  283189.333333   1.267021e+06  6.929576e+06  ...  0.054282   
3899  2.991416e+07  304998.666667   1.285287e+06  6.853465e+06  ...  0.053014   

      real_ctr  read_ratio      dur1       dur2  finish_ratio  read_files  \
11    0.217480    0.381541  5.070655  13.290064      0.348749    5.442747   
35    0.217860    0.383855  4.934453  12.855079      0.344197    5.196579   
59    0.207707    0.383028  5.047921  13.178973      0.343244    5.270167   
83    0.215168    0.379988  4.947745  13.020755      0.343732    5.249546   
107   0.208539    0.376400  4.912329  13.050842      0.350009    5.235624   
...        ...         ...       ...        ...           ...         ...   
3803  0.252604    0.347915  6.532701  18.776707      0.286471    5.979791   
3827  0.249645    0.339127  6.655131  19.624405      0.289687    6.155554   
3851  0.250395    0.342387  6.551776  19.136335      0.294718    6.058487   
3875  0.237001    0.337256  6.117320  18.138304      0.302482    5.799344   
3899  0.231388    0.319848  5.461308  17.074670      0.293127    5.199422   

       doc_dur   refresh   refresh2  
11    0.931638  4.491578  11.772442  
35    0.949570  4.392303  11.442659  
59    0.957848  4.485410  11.710395  
83    0.942503  4.442421  11.690928  
107   0.938317  4.386930  11.654988  
...        ...       ...        ...  
3803  1.092437  4.516685  12.982160  
3827  1.081222  4.458998  13.148495  
3851  1.081533  4.365080  12.749130  
3875  1.054833  4.474103  13.266288  
3899  1.050461  4.214054  13.175160  

[163 rows x 33 columns]

In [12]:
show_daily('total_total_total')

In [13]:
show_daily('video_quality_total')

In [14]:
show_daily('tuwen_quality_total')

In [15]:
show_daily('video_quality_total')

In [16]:
show_daily('tuwen_total_recommend')

In [17]:
show_daily('total_quality_total')

In [18]:
show_daily('total_total_total')